In [1]:
#!pip install lightgbm

In [2]:
#!pip install xgboost

In [3]:
#!pip install lmfit

# Importing Libraries

In [4]:
#Required Libraries
import pandas as pd
import numpy as np
pd.options.mode.chained_assignment = None


#matplotlib
import lightgbm as lgb
import xgboost as xgb
from xgboost import plot_importance, plot_tree
from sklearn.model_selection import RandomizedSearchCV, GridSearchCV
from sklearn import preprocessing, svm
from sklearn import linear_model
from sklearn.metrics import mean_squared_error, explained_variance_score
import sklearn
import matplotlib.dates as dates


#plotly library
import plotly
import plotly.graph_objects as go
import plotly.express as px
import plotly.io as pio
pio.templates.default = 'plotly_dark'
from plotly.subplots import make_subplots
from plotly.offline import init_notebook_mode, iplot
init_notebook_mode(connected = True)
import plotly.figure_factory as ff


import time
import seaborn as sns 
import datetime
from datetime import datetime, date, timedelta
from scipy import integrate, optimize
from scipy.integrate import odeint
import warnings
warnings.filterwarnings('ignore')

import os




F:\Anaconda\lib\site-packages\dask\dataframe\utils.py:15: FutureWarning: pandas.util.testing is deprecated. Use the functions in the public API at pandas.testing instead.
  import pandas.util.testing as tm


# Data

In [5]:
#Importing data from Johnn Hopkins as well as OWID

df_country = pd.read_csv('https://raw.githubusercontent.com/CSSEGISandData/COVID-19/web-data/data/cases_country.csv')
df_time = pd.read_csv('https://raw.githubusercontent.com/CSSEGISandData/COVID-19/web-data/data/cases_time.csv')
owid_covid_data = pd.read_csv('https://raw.githubusercontent.com/owid/covid-19-data/master/public/data/owid-covid-data.csv')

In [6]:
df_country.head()

Country_Region          Last_Update       Lat      Long_  Confirmed  Deaths  \
0    Afghanistan  2020-11-30 08:27:05  33.93911  67.709953    46215.0  1763.0   
1        Albania  2020-11-30 08:27:05  41.15330  20.168300    37625.0   798.0   
2        Algeria  2020-11-30 08:27:05  28.03390   1.659600    82221.0  2410.0   
3        Andorra  2020-11-30 08:27:05  42.50630   1.521800     6712.0    76.0   
4         Angola  2020-11-30 08:27:05 -11.20270  17.873900    15103.0   346.0   

   Recovered   Active  Incident_Rate  People_Tested  People_Hospitalized  \
0    36731.0   7721.0     118.718134            NaN                  NaN   
1    18481.0  18346.0    1307.422337            NaN                  NaN   
2    53204.0  26607.0     187.500671            NaN                  NaN   
3     5794.0    842.0    8686.986346            NaN                  NaN   
4     7763.0   6994.0      45.952890            NaN                  NaN   

   Mortality_Rate  UID ISO3  
0        3.814779    4  AFG  
1        2.120930    8  ALB  
2        2.931125   12  DZA  
3        1.132300   20  AND  
4        2.290936   24  AGO

In [7]:
df_time.head()

Country_Region Last_Update  Confirmed  Deaths  Recovered  Active  \
0    Afghanistan     1/22/20          0       0        NaN     NaN   
1    Afghanistan     1/23/20          0       0        NaN     NaN   
2    Afghanistan     1/24/20          0       0        NaN     NaN   
3    Afghanistan     1/25/20          0       0        NaN     NaN   
4    Afghanistan     1/26/20          0       0        NaN     NaN   

   Delta_Confirmed  Delta_Recovered  Incident_Rate  People_Tested  \
0              0.0              NaN            0.0            NaN   
1              0.0              NaN            0.0            NaN   
2              0.0              NaN            0.0            NaN   
3              0.0              NaN            0.0            NaN   
4              0.0              NaN            0.0            NaN   

   People_Hospitalized Province_State  FIPS  UID iso3 Report_Date_String  \
0                  NaN            NaN   NaN    4  AFG         2020/01/22   
1                  NaN            NaN   NaN    4  AFG         2020/01/23   
2                  NaN            NaN   NaN    4  AFG         2020/01/24   
3                  NaN            NaN   NaN    4  AFG         2020/01/25   
4                  NaN            NaN   NaN    4  AFG         2020/01/26   

   Delta_Deaths  
0           0.0  
1           0.0  
2           0.0  
3           0.0  
4           0.0

In [8]:
owid_covid_data.head()

iso_code      continent location        date  total_cases  new_cases  \
0      ABW  North America    Aruba  2020-03-13          2.0        2.0   
1      ABW  North America    Aruba  2020-03-19          NaN        NaN   
2      ABW  North America    Aruba  2020-03-20          4.0        2.0   
3      ABW  North America    Aruba  2020-03-21          NaN        NaN   
4      ABW  North America    Aruba  2020-03-22          NaN        NaN   

   new_cases_smoothed  total_deaths  new_deaths  new_deaths_smoothed  ...  \
0                 NaN           NaN         0.0                  NaN  ...   
1               0.286           NaN         NaN                  0.0  ...   
2               0.286           NaN         0.0                  0.0  ...   
3               0.286           NaN         NaN                  0.0  ...   
4               0.286           NaN         NaN                  0.0  ...   

   gdp_per_capita  extreme_poverty  cardiovasc_death_rate  \
0       35973.781              NaN                    NaN   
1       35973.781              NaN                    NaN   
2       35973.781              NaN                    NaN   
3       35973.781              NaN                    NaN   
4       35973.781              NaN                    NaN   

   diabetes_prevalence  female_smokers  male_smokers  handwashing_facilities  \
0                11.62             NaN           NaN                     NaN   
1                11.62             NaN           NaN                     NaN   
2                11.62             NaN           NaN                     NaN   
3                11.62             NaN           NaN                     NaN   
4                11.62             NaN           NaN                     NaN   

   hospital_beds_per_thousand  life_expectancy  human_development_index  
0                         NaN            76.29                      NaN  
1                         NaN            76.29                      NaN  
2                         NaN            76.29                      NaN  
3                         NaN            76.29                      NaN  
4                         NaN            76.29                      NaN  

[5 rows x 50 columns]

# Data Cleaning

In [9]:
#Let us define the columns to be cleaned into an array

cols = ['Confirmed','Deaths','Recovered','Active']

In [10]:
#Replace NaN values with empty strings

df_country[['Country_Region']] = df_country[['Country_Region']].fillna('')

In [11]:
df_country

Country_Region          Last_Update        Lat      Long_  Confirmed  \
0           Afghanistan  2020-11-30 08:27:05  33.939110  67.709953    46215.0   
1               Albania  2020-11-30 08:27:05  41.153300  20.168300    37625.0   
2               Algeria  2020-11-30 08:27:05  28.033900   1.659600    82221.0   
3               Andorra  2020-11-30 08:27:05  42.506300   1.521800     6712.0   
4                Angola  2020-11-30 08:27:05 -11.202700  17.873900    15103.0   
..                  ...                  ...        ...        ...        ...   
186  West Bank and Gaza  2020-11-30 08:27:05  31.952200  35.233200    83585.0   
187      Western Sahara  2020-11-30 08:27:05  24.215500 -12.885800       10.0   
188               Yemen  2020-11-30 08:27:05  15.552727  48.516388     2177.0   
189              Zambia  2020-11-30 08:27:05 -13.133897  27.849332    17608.0   
190            Zimbabwe  2020-11-30 08:27:05 -19.015438  29.154857     9950.0   

     Deaths  Recovered   Active  Incident_Rate  People_Tested  \
0    1763.0    36731.0   7721.0     118.718134            NaN   
1     798.0    18481.0  18346.0    1307.422337            NaN   
2    2410.0    53204.0  26607.0     187.500671            NaN   
3      76.0     5794.0    842.0    8686.986346            NaN   
4     346.0     7763.0   6994.0      45.952890            NaN   
..      ...        ...      ...            ...            ...   
186   717.0    63834.0  19034.0    1638.466653            NaN   
187     1.0        8.0      1.0       1.674116            NaN   
188   617.0     1504.0     56.0       7.299009            NaN   
189   357.0    16983.0    268.0      95.779167            NaN   
190   276.0     8482.0   1192.0      66.945091            NaN   

     People_Hospitalized  Mortality_Rate  UID ISO3  
0                    NaN        3.814779    4  AFG  
1                    NaN        2.120930    8  ALB  
2                    NaN        2.931125   12  DZA  
3                    NaN        1.132300   20  AND  
4                    NaN        2.290936   24  AGO  
..                   ...             ...  ...  ...  
186                  NaN        0.857809  275  PSE  
187                  NaN       10.000000  732  ESH  
188                  NaN       28.341755  887  YEM  
189                  NaN        2.027488  894  ZMB  
190                  NaN        2.773869  716  ZWE  

[191 rows x 14 columns]

In [12]:
#Replace the NaN in numerical columns with 0

df_country[cols] = df_country[cols].fillna(0)

In [13]:
#Replace the United Kingdom with just UK

df_country.loc[df_country['Country_Region'] == "United Kingdom", "Country_Region"] = "UK"

In [14]:
df_country.head()

Country_Region          Last_Update       Lat      Long_  Confirmed  Deaths  \
0    Afghanistan  2020-11-30 08:27:05  33.93911  67.709953    46215.0  1763.0   
1        Albania  2020-11-30 08:27:05  41.15330  20.168300    37625.0   798.0   
2        Algeria  2020-11-30 08:27:05  28.03390   1.659600    82221.0  2410.0   
3        Andorra  2020-11-30 08:27:05  42.50630   1.521800     6712.0    76.0   
4         Angola  2020-11-30 08:27:05 -11.20270  17.873900    15103.0   346.0   

   Recovered   Active  Incident_Rate  People_Tested  People_Hospitalized  \
0    36731.0   7721.0     118.718134            NaN                  NaN   
1    18481.0  18346.0    1307.422337            NaN                  NaN   
2    53204.0  26607.0     187.500671            NaN                  NaN   
3     5794.0    842.0    8686.986346            NaN                  NaN   
4     7763.0   6994.0      45.952890            NaN                  NaN   

   Mortality_Rate  UID ISO3  
0        3.814779    4  AFG  
1        2.120930    8  ALB  
2        2.931125   12  DZA  
3        1.132300   20  AND  
4        2.290936   24  AGO

# Exploratory Data Analysis

## Top 10 Countries with highest Death Cases

In [15]:
#Finding out the Top 10 Countries with the highest amount of deaths.

Top10_Countries_death = df_country.drop(['Last_Update', 'Lat','Long_','Incident_Rate','People_Tested','People_Hospitalized','Mortality_Rate','UID','ISO3'], axis=1) 
Top10_Countries_death = Top10_Countries_death.nlargest(10, 'Deaths')

In [17]:
Top10_Countries_death.head(10)

Country_Region   Confirmed    Deaths  Recovered     Active
176             US  13384651.0  266875.0  5065030.0  8052746.0
23          Brazil   6314740.0  172833.0  5581436.0   560471.0
79           India   9431691.0  137139.0  8847600.0   446952.0
114         Mexico   1107071.0  105655.0   818397.0   183019.0
180             UK   1621305.0   58342.0     3514.0  1559449.0
85           Italy   1585178.0   54904.0   734503.0   795771.0
62          France   2270573.0   52410.0   167005.0  2051158.0
81            Iran    948749.0   47874.0   658292.0   242583.0
160          Spain   1628208.0   44668.0   150376.0  1433164.0
141         Russia   2275936.0   39491.0  1763493.0   472952.0

## Top 10 Countries with highest Confirmed Cases

In [18]:
#Finding out the Top 10 Countries with the highest amount of confirmed cases.

Top10_Countries_Confirmed = df_country.drop(['Last_Update', 'Lat','Long_','Incident_Rate','People_Tested','People_Hospitalized','Mortality_Rate','UID','ISO3'], axis=1) 
Top10_Countries_Confirmed = Top10_Countries_Confirmed.nlargest(10, 'Confirmed')

In [19]:
Top10_Countries_Confirmed.head(10)

Country_Region   Confirmed    Deaths  Recovered     Active
176             US  13384651.0  266875.0  5065030.0  8052746.0
79           India   9431691.0  137139.0  8847600.0   446952.0
23          Brazil   6314740.0  172833.0  5581436.0   560471.0
141         Russia   2275936.0   39491.0  1763493.0   472952.0
62          France   2270573.0   52410.0   167005.0  2051158.0
160          Spain   1628208.0   44668.0   150376.0  1433164.0
180             UK   1621305.0   58342.0     3514.0  1559449.0
85           Italy   1585178.0   54904.0   734503.0   795771.0
6        Argentina   1418807.0   38473.0  1249843.0   130491.0
37        Colombia   1308376.0   36584.0  1204452.0    67340.0

## Top 10 Countries with highest Recovered Cases

In [20]:
#Finding out the Top 10 Countries with the highest amount of recovered cases.

Top10_Countries_Recovered = df_country.drop(['Last_Update', 'Lat','Long_','Incident_Rate','People_Tested','People_Hospitalized','Mortality_Rate','UID','ISO3'], axis=1) 
Top10_Countries_Recovered = Top10_Countries_Recovered.nlargest(10, 'Recovered')

In [21]:
Top10_Countries_Recovered.head(10)

Country_Region   Confirmed    Deaths  Recovered     Active
79           India   9431691.0  137139.0  8847600.0   446952.0
23          Brazil   6314740.0  172833.0  5581436.0   560471.0
176             US  13384651.0  266875.0  5065030.0  8052746.0
141         Russia   2275936.0   39491.0  1763493.0   472952.0
6        Argentina   1418807.0   38473.0  1249843.0   130491.0
37        Colombia   1308376.0   36584.0  1204452.0    67340.0
135           Peru    962530.0   35923.0   893061.0    33546.0
114         Mexico   1107071.0  105655.0   818397.0   183019.0
85           Italy   1585178.0   54904.0   734503.0   795771.0
66         Germany   1063752.0   16306.0   730797.0   316649.0

## Top 10 Countries with highest Active Cases

In [22]:
#Finding out the Top 10 Countries with the highest amount of active cases.

Top10_Countries_Active = df_country.drop(['Last_Update', 'Lat','Long_','Incident_Rate','People_Tested','People_Hospitalized','Mortality_Rate','UID','ISO3'], axis=1) 
Top10_Countries_Active = Top10_Countries_Active.nlargest(10, 'Active')

In [23]:
Top10_Countries_Active.head(10)

Country_Region   Confirmed    Deaths  Recovered     Active
176             US  13384651.0  266875.0  5065030.0  8052746.0
62          France   2270573.0   52410.0   167005.0  2051158.0
180             UK   1621305.0   58342.0     3514.0  1559449.0
160          Spain   1628208.0   44668.0   150376.0  1433164.0
85           Italy   1585178.0   54904.0   734503.0   795771.0
23          Brazil   6314740.0  172833.0  5581436.0   560471.0
16         Belgium    576599.0   16547.0        0.0   560052.0
123    Netherlands    527336.0    9426.0     6921.0   510989.0
141         Russia   2275936.0   39491.0  1763493.0   472952.0
79           India   9431691.0  137139.0  8847600.0   446952.0

In [24]:
#Top 10 Countries with the highest number of death cases.

fig = px.bar(Top10_Countries_death.sort_values('Deaths',ascending=False)[:20][::-1],x='Deaths',y='Country_Region',title='Top 10 Countries with highest number of Death Cases',text='Deaths', height=900, orientation='h')

plotly.offline.iplot(fig)

## World top 10 countries with all types of COVID-19 Cases.

In [25]:
#Plotting all 4 types in cases in one graph itself.

fig = make_subplots(
    rows=2, cols=2,
    specs=[[{"type": "bar"}, {"type": "bar"}],
           [{"type": "bar"}, {"type": "bar"}]],
    subplot_titles=("Top 10 Countries with Confirmed Cases","Top 10 Countries with Death Cases", "Top 10 Countries with Recovered Cases", "Top 10 Countries with Active Cases")
)

fig.add_trace(go.Bar(name='Confirmed',text='Confirmed', x=Top10_Countries_Confirmed['Country_Region'], y=Top10_Countries_Confirmed['Confirmed']),
              row=1, col=1)


fig.add_trace(go.Bar(name='Deaths',text='Deaths', x=Top10_Countries_death['Country_Region'], y=Top10_Countries_death['Deaths']),
              row=1, col=2)

fig.add_trace(go.Bar(name='Recovered', text='Recovered',x=Top10_Countries_Active['Country_Region'], y=Top10_Countries_Active['Recovered']),
              row=2, col=1)

fig.add_trace(go.Bar(name='Active',text='Active', x=Top10_Countries_Recovered['Country_Region'], y=Top10_Countries_Recovered['Active']),
              row=2, col=2)

fig.update_layout(height=700,title_text="World top 10 countries with Covid-19 Cases", showlegend=False)

#fig.show()
plotly.offline.iplot(fig)

In [26]:
#Comparing the cases of the countries with each other.

fig = go.Figure(data=[
    go.Bar(name='Confirmed', x=Top10_Countries_death['Country_Region'], y=Top10_Countries_death['Confirmed']),
     go.Bar(name='Deaths', x=Top10_Countries_death['Country_Region'], y=Top10_Countries_death['Deaths']),
     go.Bar(name='Recovered', x=Top10_Countries_death['Country_Region'], y=Top10_Countries_death['Recovered']),
])
# Change the bar mode
fig.update_layout(barmode='group')
#fig.show()
plotly.offline.iplot(fig)

=> India is among the countries with the highest recovery cases.

In [27]:
#Animation of the Virus' spread over time.

formated_gdf = df_time.groupby(['Report_Date_String', 'Country_Region'])['Confirmed'].max()
formated_gdf = formated_gdf.reset_index()
formated_gdf['Report_Date_String'] = pd.to_datetime(formated_gdf['Report_Date_String'])
formated_gdf['Report_Date_String'] = formated_gdf['Report_Date_String'].dt.strftime('%m/%d/%Y')
formated_gdf['size'] = formated_gdf['Confirmed'].pow(0.3)

fig = px.scatter_geo(formated_gdf, locations="Country_Region", locationmode='country names', 
                     color="Confirmed", size='size', hover_name="Country_Region", 
                     range_color= [0, 1500], 
                     projection="natural earth", animation_frame="Report_Date_String", 
                     title='COVID-19: Spread Over Time', color_continuous_scale="portland")
# fig.update(layout_coloraxis_showscale=False)
#fig.show()
plotly.offline.iplot(fig)



In [28]:
#Using the OWID data for new cases and deaths.

owid_covid_data_Selected = owid_covid_data[['date','new_cases','new_deaths']]

owid_covid_data_Selected.tail()


date  new_cases  new_deaths
59967  2020-11-25        NaN         NaN
59968  2020-11-26        NaN         NaN
59969  2020-11-27        NaN         NaN
59970  2020-11-28        NaN         NaN
59971  2020-11-29        NaN         NaN

In [29]:
#Resetting the index and converting date string to datetime format for both dataframes.

owid_covid_newcases = owid_covid_data_Selected.groupby(['date'])['new_cases'].sum()
owid_covid_newcases = owid_covid_newcases.reset_index()
owid_covid_newcases['date'] = pd.to_datetime(owid_covid_newcases['date'])
owid_covid_newcases['date'] = owid_covid_newcases['date'].dt.strftime('%m/%d/%Y')
owid_covid_newcases.head()

owid_covid_newdeaths = owid_covid_data_Selected.groupby(['date'])['new_deaths'].sum()
owid_covid_newdeaths = owid_covid_newdeaths.reset_index()
owid_covid_newdeaths['date'] = pd.to_datetime(owid_covid_newdeaths['date'])
owid_covid_newdeaths['date'] = owid_covid_newdeaths['date'].dt.strftime('%m/%d/%Y')
owid_covid_newdeaths.head()


date  new_deaths
0  12/31/2019         0.0
1  01/01/2020         0.0
2  01/02/2020         0.0
3  01/03/2020         0.0
4  01/04/2020         0.0

In [30]:
#Plotting the new cases and deaths over time.

fig = go.Figure(data=[
    go.Line(x=owid_covid_newcases['date'], y=owid_covid_newcases['new_cases'],mode='lines',name='New Case'),
     go.Line(x=owid_covid_newdeaths['date'], y=owid_covid_newdeaths['new_deaths'],mode='lines',name='Death'),
])

fig.update_layout(
    title="TrendLine - World Death and new cases over the time",
    yaxis_title="New or Death Cases",
    xaxis_title="Date",
    showlegend=True
)
#fig.show()
plotly.offline.iplot(fig)

In [37]:
#Finding out the Top 10 countries with the highest covid death r

Top10_Countries = Top10_Countries_death[['Country_Region']]
Top10_Countries.loc[Top10_Countries['Country_Region'] == "UK", "Country_Region"] = "United Kingdom"
Top10_Countries.loc[Top10_Countries['Country_Region'] == "US", "Country_Region"] = "United States"
filter_list = Top10_Countries['Country_Region']. values. tolist()
owid_Top10_Countries = owid_covid_data.loc[owid_covid_data['location'].isin(filter_list)]

Top10_gdp_per_capita =  owid_Top10_Countries.groupby(['location'])['gdp_per_capita'].max().to_frame(name = 'gdp_per_capita').reset_index()
Top10_cvd_death_rate =  owid_Top10_Countries.groupby(['location'])['total_deaths'].max().to_frame(name = 'total_deaths').reset_index()
Top10_diabetes_prevalence =  owid_Top10_Countries.groupby(['location'])['diabetes_prevalence'].max().to_frame(name = 'diabetes_prevalence').reset_index()
Top10_female_smokers =  owid_Top10_Countries.groupby(['location'])['female_smokers'].max().to_frame(name = 'female_smokers').reset_index()
Top10_male_smokers =  owid_Top10_Countries.groupby(['location'])['male_smokers'].max().to_frame(name = 'male_smokers').reset_index()
Top10_hospital_beds_per_100k =  owid_Top10_Countries.groupby(['location'])['hospital_beds_per_thousand'].max().to_frame(name = 'hospital_beds_per_100k').reset_index()

Top10_cvd_death_rate.head(10)

location  total_deaths
0          Brazil      172561.0
1          France       52127.0
2           India      136696.0
3            Iran       47486.0
4           Italy       54363.0
5          Mexico      105459.0
6          Russia       39527.0
7           Spain       44668.0
8  United Kingdom       58030.0
9   United States      266063.0

In [32]:
#10 countries with the lowest gross domestic product per capita

Bottom10_Countries_death = df_country.drop(['Last_Update', 'Lat','Long_','Incident_Rate','People_Tested','People_Hospitalized','Mortality_Rate','UID','ISO3'], axis=1) 
Bottom10_Countries_death = Bottom10_Countries_death.loc[(Bottom10_Countries_death['Deaths'] >= 1)].nsmallest(10, 'Deaths')
Bottom10_Countries_death.head(10)
Bottom10_Countries = Bottom10_Countries_death[['Country_Region']]
Bottom10_Countries.loc[Bottom10_Countries['Country_Region'] == "UK", "Country_Region"] = "United Kingdom"
Bottom10_Countries.loc[Bottom10_Countries['Country_Region'] == "US", "Country_Region"] = "United States"
filter_list = Bottom10_Countries['Country_Region']. values. tolist()
owid_Bottom10_Countries = owid_covid_data.loc[owid_covid_data['location'].isin(filter_list)]

Bottom10_gdp_per_capita =  owid_Bottom10_Countries.groupby(['location'])['gdp_per_capita'].max().to_frame(name = 'gdp_per_capita').reset_index()
Bottom10_cvd_death_rate =  owid_Bottom10_Countries.groupby(['location'])['total_deaths'].max().to_frame(name = 'total_deaths').reset_index()
Bottom10_diabetes_prevalence =  owid_Bottom10_Countries.groupby(['location'])['diabetes_prevalence'].max().to_frame(name = 'diabetes_prevalence').reset_index()
Bottom10_female_smokers =  owid_Bottom10_Countries.groupby(['location'])['female_smokers'].max().to_frame(name = 'female_smokers').reset_index()
Bottom10_male_smokers =  owid_Bottom10_Countries.groupby(['location'])['male_smokers'].max().to_frame(name = 'male_smokers').reset_index()
Bottom10_hospital_beds_per_100k =  owid_Bottom10_Countries.groupby(['location'])['hospital_beds_per_thousand'].max().to_frame(name = 'hospital_beds_per_100k').reset_index()
Bottom10_gdp_per_capita.head(10)


location  gdp_per_capita
0  Antigua and Barbuda       21490.943
1             Barbados       16978.068
2               Brunei       71809.251
3              Burundi         702.225
4              Comoros        1413.890
5                 Fiji        8702.975
6               Monaco             NaN
7          Saint Lucia       12951.839
8       Western Sahara             NaN

In [33]:
#Comparing the top 10 and the bottom 10 countries in the COVID death list.

fig = make_subplots(
    rows=1, cols=2,
    specs=[[{"type": "bar"}, {"type": "bar"}]],
    subplot_titles=("Top 10 Countries with Death Cases","Bottom 10 Countries with Death Cases")
)

fig.add_trace(go.Bar(name='Deaths',text='Deaths', x=Top10_Countries_death['Country_Region'], y=Top10_Countries_death['Deaths']),
              row=1, col=1)

fig.add_trace(go.Bar(name='Deaths',text='Deaths', x=Bottom10_Countries_death['Country_Region'], y=Bottom10_Countries_death['Deaths']),
              row=1, col=2)
fig.update_layout(height=900,title_text="Comaprison - COVID Death Cases", showlegend=False)

#fig.show()
plotly.offline.iplot(fig)

In [34]:
#Saving the dataframes into csvs.

df_country.to_csv('df_country.csv')
df_time.to_csv('df_time.csv')
owid_covid_data.to_csv('owid_covid_data.csv')